### Basic Boolean Search in Documents

### Objective
Expand the simple term search functionality to include Boolean search capabilities. This will allow users to perform more complex queries by combining multiple search terms using Boolean operators.

### Problem Description
You must enhance the existing search engine from the previous exercise to support Boolean operators: AND, OR, and NOT. This will enable the retrieval of documents based on the logical relationships between multiple terms.

### Requirements

### Step 1: Update Data Preparation
Ensure that the documents are still loaded and preprocessed from the previous task. The data should be clean and ready for advanced querying.

In [1]:
import os
import re

In [2]:
def cargar_archivo(ruta_archivo):
    with open(ruta_archivo, "r", encoding="utf-8") as archivo:
        contenido = archivo.read()
    return contenido


In [3]:
def tokenizar_texto(texto):
    palabras = re.findall(r'\b\d{2,}\b|\b\w+\b', texto)
    return palabras


In [4]:
def limpiar_texto(palabras):
    palabras_limpias = [palabra.lower() for palabra in palabras if palabra.isalpha()]
    return palabras_limpias

In [5]:
def procesar_archivo(ruta_archivo):
    contenido = cargar_archivo(ruta_archivo)
    palabras_tokenizadas = tokenizar_texto(contenido)
    palabras_limpias = limpiar_texto(palabras_tokenizadas)
    return palabras_limpias

In [6]:
def preparar_archivos_tokenizados(directorio):
    archivos_tokenizados = {}
    for nombre_archivo in os.listdir(directorio):
        if nombre_archivo.endswith(".txt"):
            ruta_archivo = os.path.join(directorio, nombre_archivo)
            palabras_procesadas = procesar_archivo(ruta_archivo)
            archivos_tokenizados[nombre_archivo] = palabras_procesadas
    return archivos_tokenizados

### Step 2: Create an Inverted Index
Create an inverted index from the documents. This index maps each word to the set of document IDs in which that word appears. This facilitates word lookup in the search process.

In [7]:
def crear_indice_invertido(archivos_tokenizados):
    indice_invertido = {}
    for nombre_archivo, palabras in archivos_tokenizados.items():
        for palabra in palabras:
            if palabra in indice_invertido:
                indice_invertido[palabra].add(nombre_archivo)
            else:
                indice_invertido[palabra] = {nombre_archivo}
    return indice_invertido

### Step 3: Query Processing
Parse the Query: Implement a function to parse the input query to identify the terms and operators.
Search Documents: Based on the parsed query, implement the logic to retrieve and rank the documents according to the Boolean expressions.

In [8]:
def analizar_consulta(consulta):
    terminos = consulta.split()
    operadores_booleanos = [term for term in terminos if term in ["AND", "OR", "NOT"]]
    terminos = [term for term in terminos if term not in ["AND", "OR", "NOT"]]
    return terminos, operadores_booleanos

In [9]:
def buscar_documentos(terminos, operadores_booleanos, indice_invertido):
    documentos_coincidentes = None
    for i, termino in enumerate(terminos):
        documentos_termino = indice_invertido.get(termino, set())
        if operadores_booleanos and i < len(operadores_booleanos):
            operador = operadores_booleanos[i]
            if operador == "AND":
                documentos_coincidentes = documentos_termino if documentos_coincidentes is None else documentos_coincidentes & documentos_termino
            elif operador == "OR":
                documentos_coincidentes = documentos_termino if documentos_coincidentes is None else documentos_coincidentes | documentos_termino
            elif operador == "NOT":
                documentos_coincidentes -= documentos_termino
        else:
            documentos_coincidentes = documentos_termino if documentos_coincidentes is None else documentos_coincidentes & documentos_termino
    return documentos_coincidentes


### Step 4: Displaying Results
Output the Results: Display the documents that match the query criteria. Include functionalities to handle queries that result in no matching documents.

In [10]:
def mostrar_resultados(documentos_coincidentes):
    if documentos_coincidentes:
        print("\nDocumentos que coinciden con la consulta:")
        for documento in documentos_coincidentes:
            print("- ", documento)
    else:
        print("No se encontraron documentos que coincidan con la consulta.")

def obtener_consulta_usuario():
    consulta = input("Ingrese la consulta de búsqueda: ")
    return consulta

In [11]:
directorio = r"D:\Kevin\Documents\EPN\2024A\Recuperación de Información\ir24a\week01\data"
archivos_tokenizados = preparar_archivos_tokenizados(directorio)
indice_invertido = crear_indice_invertido(archivos_tokenizados)

In [12]:

consulta_usuario = obtener_consulta_usuario()
terminos, operadores_booleanos = analizar_consulta(consulta_usuario)
documentos_coincidentes = buscar_documentos(terminos, operadores_booleanos, indice_invertido)
mostrar_resultados(documentos_coincidentes)



Documentos que coinciden con la consulta:
-  pg76.txt
-  pg120.txt
-  pg45.txt
-  pg145.txt
-  pg11.txt
-  pg100.txt
-  pg74.txt
-  pg46.txt
-  pg98.txt
-  pg55.txt
-  pg16.txt
-  pg43.txt
-  pg84.txt
-  pg174.txt


In [13]:

def crear_matriz_indices(archivos_tokenizados):
    matriz_indices = {}
    for nombre_archivo, palabras in archivos_tokenizados.items():
        for palabra in palabras:
            if palabra in matriz_indices:
                matriz_indices[palabra][nombre_archivo] = 1
            else:
                matriz_indices[palabra] = {archivo: 0 for archivo in archivos_tokenizados}
                matriz_indices[palabra][nombre_archivo] = 1
    return matriz_indices


### Index Matrix

In [14]:
def mostrar_matriz_indices(matriz_indices):
    print("\nMatriz de índices:")
    print("{: <15}".format("Palabra"), end="")
    for nombre_archivo in matriz_indices[next(iter(matriz_indices))]:
        print("{: <10}".format(nombre_archivo), end="")
    print()
    for palabra, presencias in matriz_indices.items():
        print("{: <15}".format(palabra), end="")
        for nombre_archivo in matriz_indices[next(iter(matriz_indices))]:
            print("{: <10}".format(presencias.get(nombre_archivo, 0)), end="")
        print()


In [15]:
# Luego de obtener la consulta y los documentos coincidentes

# Preparar la matriz de índices
matriz_indices = crear_matriz_indices(archivos_tokenizados)



In [16]:
# Mostrar la matriz de índices
mostrar_matriz_indices(matriz_indices)


Matriz de índices:
Palabra        pg100.txt pg11.txt  pg120.txt pg145.txt pg16.txt  pg174.txt pg43.txt  pg45.txt  pg46.txt  pg55.txt  pg74.txt  pg76.txt  pg84.txt  pg98.txt  
the            1         1         1         1         1         1         1         1         1         1         1         1         1         1         
project        1         1         1         1         1         1         1         1         1         1         1         1         1         1         
gutenberg      1         1         1         1         1         1         1         1         1         1         1         1         1         1         
ebook          1         1         1         1         1         1         1         1         1         1         1         1         1         1         
of             1         1         1         1         1         1         1         1         1         1         1         1         1         1         
complete       1         0         1        

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



0         0         0         0         0         0         0         0         0         0         
enfranchised   1         0         0         0         0         0         0         0         0         0         0         0         1         0         
betroths       1         0         0         0         0         0         0         0         0         0         0         0         0         0         
unquietness    1         0         0         0         0         0         0         0         0         0         0         0         0         0         
chick          1         0         0         1         0         0         0         0         0         0         0         0         0         0         
perfumer       1         0         0         0         0         0         0         0         0         0         0         0         0         0         
whipt          1         0         0         0         0         0         0         0         0         0         0   

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

